In [228]:
import pandas as pd
import numpy as np


In [219]:
pd.__version__

'0.23.0'

In [255]:
clothes=pd.read_csv("all.csv",index_col=0)
print(clothes.shape)

(10610, 12)


In [156]:
clothes.sample(n=10)

Unnamed: 0  \
2289   2289         
4809   4809         
10024  10024        
608    608          
4106   4106         
595    595          
6204   6204         
9321   9321         
3003   3003         
4105   4105         

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  alltext  \
2289   Schoolboy Crewneck Tee Fits true to size, order your normal size,Designed for a contemporary fit,Model measurements: 5'10" height, 33.5" bust, 23.5" waist, 34.5" hips, wearing a size small,Ribbed crewneck, short sleeves,Side slits, slim silhouette, slub knit,Cotton,Hand wash,Imported,Web ID: 2488554                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                         
4809   Rainbeau Curve Zebra Print Racerback Bra Non-padded cups,Zip front,Zebra-print panels,Go wild,Supportive underband for a secure fit,Perforated mesh panels,Racer back with cut-out detail,Form-fitting design Soft-touch fabric,The kind that stretches,Main: 88% Cotton, 12% Spandex\t,Mesh: 95% Polyester, 5% Spandex, Fabric 2: 75% Nylon, 25% Spandex                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            
10024  Boohoo Oversized Midi T-Shirt Dress A wardrobe staple,V-neck,Split sides,Oversized fit,More room for activities Soft-touch stretch jersey,Why complicate things?,Main: 95% Cotton, 5% Spandex.                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       
608    Dress with Ties Short dress in woven viscose fabric with a V-neck an

In [ ]:
import re
toy=clothes.description.iloc[1:20] #create toy regex
toy= toy.apply(lambda x: re.sub('[^\w\s]','', x)) #remove all punctuation
toy_tokens = toy.apply(lambda x: x.split())
toy

In [ ]:
toy

In [ ]:
top=clothes[clothes.category=="Top"]

In [ ]:
dress=clothes[clothes.category=="Dress"]

In [ ]:
top.iloc[:,10]

In [ ]:
clothes.alltext.sample(n=10)

In [ ]:
import gensim
from gensim.models import Word2Vec
from gensim.utils import simple_preprocess


class MySentences(object): 
    def __iter__(self):
        for i in range(clothes.shape[0]):
            yield clothes.iloc[i,10]#simple_preprocess(clothes.iloc[i,10])

- `min-count` is for pruning the internal dictionary. Words that appear only once or twice in a billion-word corpus are probably uninteresting typos and garbage. In addition, there’s not enough data to make any meaningful training on those words, so it’s best to ignore them. A reasonable value for min_count is between 0-100, depending on the size of your dataset.

- `size` is the length of your output vector of each word, which is also the number of neurons in the hidde layer.

- `workers` parameter has only effect if you have Cython installed. Without Cython, you’ll only be able to use one core because of the GIL (and word2vec training will be miserably slow).

In [ ]:
assert gensim.models.doc2vec.FAST_VERSION > -1, "this will be painfully slow otherwise"

In [ ]:
%%time
import multiprocessing
import os
cores = multiprocessing.cpu_count()

if not os.path.exists('models/word2vec.model'):
    print("start traing word2vec model...")
    #sentences = MySentences() # a memory-friendly iterator
    word2vec_model = gensim.models.Word2Vec(vec, min_count=20, size=10, workers=cores)
    if not os.path.exists('models'):
        os.makedirs('models')
        word2vec_model.save('models/word2vec.model')
    else:
        word2vec_model.save('models/word2vec.model')
else:
    word2vec_model = Word2Vec.load('models/word2vec.model')
    

In [ ]:
word2vec_model.wv.get_vector("cotton")

In [ ]:
%%time
mode=gensim.models.Word2Vec(vec, min_count=10, size=300, workers=cores, iter=20,window=10)

In [ ]:
mode.wv.get_vector("rayon")

In [ ]:
mode.wv.most_similar(positive='black') 

In [ ]:
#from https://medium.com/@aneesha/using-tsne-to-plot-a-subset-of-similar-words-from-word2vec-bb8eeaea6229
import matplotlib.pyplot as plt
 
from sklearn.manifold import TSNE
def display_closestwords_tsnescatterplot(model, word):
    
    arr = np.empty((0,300), dtype='f')
    word_labels = [word]

    # get close words
    close_words = model.similar_by_word(word)
    
    # add the vector for each of the closest words to the array
    arr = np.append(arr, np.array([model[word]]), axis=0)
    for wrd_score in close_words:
        wrd_vector = model[wrd_score[0]]
        word_labels.append(wrd_score[0])
        arr = np.append(arr, np.array([wrd_vector]), axis=0)
        
    # find tsne coords for 2 dimensions
    tsne = TSNE(n_components=2, random_state=2)
    np.set_printoptions(suppress=True)
    Y = tsne.fit_transform(arr)

    x_coords = Y[:, 0]
    y_coords = Y[:, 1]
    # display scatter plot
    plt.scatter(x_coords, y_coords)

    for label, x, y in zip(word_labels, x_coords, y_coords):
        plt.annotate(label, xy=(x, y), xytext=(0, 0), textcoords='offset points')
    plt.xlim(x_coords.min()+0.00005, x_coords.max()+0.00005)
    plt.ylim(y_coords.min()+0.00005, y_coords.max()+0.00005)
    plt.show()

In [ ]:
display_closestwords_tsnescatterplot(mode, 'black')

In [ ]:
# tag: category #tag price

### Doc to vec

In [ ]:
from gensim.models.doc2vec import Doc2Vec, TaggedDocument

In [ ]:
# convert (Viscose 100%) to (Viscose100%, Viscose)
# convert (100% Viscose) to (Viscose100%, Viscose)

In [ ]:
toy=clothes.copy()
#list of clothing brand to take out from alltext
ls = r'|'.join(('ASOS', "YAS", "Ditsy", "Noisy", "May", "Ted","Baker", "River","Island", "Karen","Scott","PrettyLittleThing","Roxy","DESIGN","Chi",
               "Alfani","Boohoo","Sofie","Schnoor","Ellesse", "Jeannie","TFNC","Sacred", "Hawk","Urban","Bliss","Puma","adidas", "Stella"))
#toy.alltext= toy.alltext.apply(lambda x: re.sub('[^\w\s]','', x)) #remove all punctuation
toy.alltext= toy.alltext.apply(lambda x: re.sub("-",'', x))
toy.iloc[1:4]

In [276]:
%%time
pd.set_option('display.max_colwidth', -1)
import re
toy=clothes.copy()
#list of clothing brand to take out from alltext
ls = r'|'.join(('ASOS', "YAS", "Ditsy", "Noisy", "May", "Ted","Baker", "River","Island", "Karen","Scott","PrettyLittleThing","Roxy","DESIGN","Chi",
               "Alfani","Boohoo","Sofie","Schnoor","Ellesse", "Jeannie","TFNC","Sacred", "Hawk","Urban","Bliss","Puma","adidas", "Stella"))
#toy.alltext= toy.alltext.apply(lambda x: re.sub('[^\w\s]','', x)) #remove all punctuation
toy.alltext= toy.alltext.apply(lambda x: re.sub("-",'', x))
toy.alltext= toy.alltext.apply(lambda x: re.sub(ls,'', x))
toy.alltext= toy.alltext.apply(lambda x: x.lower())

# convert (100% Viscose) to (Viscose100%, Viscose)
#feature engineering!!!!!
toy.alltext=toy.alltext.apply(lambda x: re.sub("(\d+\%)+\s+([a-z]+)|([a-z]+)\s+(\d+\%)", "\\1\\2  \\3\\4",x))
toy.alltext=toy.alltext.apply(lambda x: re.sub("(\d+\%)+([a-z]+)|([a-z]+)+(\d+\%)", "\\2  \\2\\1  \\3  \\3\\4",x))
#toy.alltext=toy.alltext.apply(lambda x: x.split())

# remove words:
# cm
# size,
# ‘Web ID:’

Wall time: 1min 47s


In [277]:
toy.alltext=toy.alltext.apply(lambda x: re.sub('[^\w\s]','', x)) 
#toy.alltext=toy.alltext.apply(lambda x: x.split())

In [ ]:
vec

In [ ]:
tovec=', '.join(toy.alltext)
tovec=tovec.split(" ")

In [ ]:
tovec

In [ ]:
#a=toy.alltext.apply(lambda x: x.split())
new=toy.alltext
#new=toy.alltext.apply(lambda x: re.sub(",", " ",x))
ls=[]
for i in new:
    ls.append(i)
#     for j in i:
#         ls.append(j)
map(float, '1,2,3,4'.split(','))

In [ ]:
toy.sample(n=20)

In [ ]:
import re
toy1=clothes.copy()
toy1=toy1[toy1.product_name.isna()==False]
new=toy1["product_name"][5000:].apply(lambda x: x.split())
[x[0:3] for x in new]
#toy1.product_name#.apply(lambda x: re.sub('[^\w\s]','', x))
#toy.product_name=toy.product_name.apply(lambda x: x.split())


In [ ]:
# MyDocs reading from a data frame
class MyDocs(object):
    def __iter__(self):
        for i in range(toy.shape[0]):
            yield TaggedDocument(words=toy.iloc[i,10], tags=['%s' % toy.iloc[i,9]])

In [ ]:
%%time

if not os.path.exists('models/doc2vec.model'):
    print("start traing doc2vec model...")
    documents = MyDocs()
    doc2vec_model = Doc2Vec(dm=1, dbow_words=1, vector_size=100, window=5, min_count=10, workers=cores) #dm: distributed model #vector_size is minimun count
    doc2vec_model.build_vocab(documents)
    doc2vec_model.train(documents, total_examples=doc2vec_model.corpus_count, epochs=doc2vec_model.epochs)
    if not os.path.exists('models'):
        os.makedirs('models')
        doc2vec_model.save('models/doc2vec.model')
    else:
        doc2vec_model.save('models/doc2vec.model')
else:
    doc2vec_model = Doc2Vec.load('models/doc2vec.model')

In [ ]:
doc2vec_model.wv.most_similar(positive=["vneck","tshirt"], negative="asos")

In [ ]:
print(doc2vec_model.docvecs.most_similar('La La Land', topn=20))

In [ ]:
def vec(w):
    return words.loc[w].as_matrix()
vec("cotton")

 ### Pre-trained

In [224]:
%%time
import numpy as np
def loadGloveModel(gloveFile):
    print ("Loading Glove Model")
    f = open(gloveFile,'r',encoding="utf8")#
    model = {}
    for line in f:
        splitLine = line.split()
        word = splitLine[0]
        embedding = np.array([float(val) for val in splitLine[1:]])
        model[word] = embedding
        if len(model) % 19000== 0:
            print("+1")
    print ("Done.",len(model)," words loaded!")
    return model

embeddingmodel= loadGloveModel("glove.42B.300d.txt")

Loading Glove Model
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
+1
Done. 1917494  words loaded!
Wall time: 8min 51s


In [215]:
print(len(embeddingmodel["import"]))

300


In [140]:
%%time
embedding_dim = 300
# max_words=
# embedding_matrix = np.zeros((max_words, embedding_dim))

k=0
for i in toy.alltext:
    i=i.split()
    max_words=len(i)
    embedding_matrix = np.zeros((max_words, embedding_dim))
    for j in i:
        embedding_vector=embeddingmodel.get(j)
        if embedding_vector is not None:
            embedding_matrix[k] = embedding_vector
            print(k)
            

# embedding_matrix = np.zeros((max_words, embedding_dim))
# for word, i in word_index.items():
#     embedding_vector = embeddings_index.get(word)
#     if i < max_words:
#         if embedding_vector is not None:
#             # Words not found in embedding index will be all-zeros.
#             embedding_matrix[i] = embedding_vector

21
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
14
0
0
0
0
0
0
0
0
0
0
0
0
0
23
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
31
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
13
0
0
0
0
0
0
0
0
0
0
0
0
0
18
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
13
0
0
0
0
0
0
0
0
0
0
0
0
0
7
0
0
0
0
0
0
0
10
0
0
0
0
0
0
0
28
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
16
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
7
0
0
0
0
0
0
0
21
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
10
0
0
0
0
0
0
0
21
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
11
0
0
0
0
0
0
0
0
0
0
0
18
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
14
0
0
0
0
0
0
0
0
0
0
10
0
0
0
0
0
0
0
0
0
0
15
0
0
0
0
0
0
0
0
0
0
0
0
0
27
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
30
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
20
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
22
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
26
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
27
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
12
0
0
0
0
0
0
0
0
0
0
0
29
0
0
0
0
0
0
0
0
0
0


27
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
29
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
21
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
23
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
32
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
25
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
27
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
24
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
30
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
21
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
17
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
13
0
0
0
0
0
0
0
0
0
0
0
7
0
0
0
0
0
0
0
16
0
0
0
0
0
0
0
0
0
0
0
0
21
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
21
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
28
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
17
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
28
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
14
0
0
0
0
0
0
0
0
0
0
0
0
0
20
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
15
0
0
0
0
0
0
0
0
0
0
0
0
0
25
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
17
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0

0
0
0
0
0
0
0
18
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
7
0
0
0
0
0
0
0
23
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
24
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
14
0
0
0
0
0
0
0
0
0
0
0
0
0
0
13
0
0
0
0
0
0
0
0
0
0
0
0
0
20
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
23
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
23
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
30
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
20
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
24
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
18
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
17
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
19
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
25
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
13
0
0
0
0
0
0
0
0
0
0
0
0
0
13
0
0
0
0
0
0
0
0
0
0
0
0
0
13
0
0
0
0
0
0
0
0
0
0
0
0
0
10
0
0
0
0
0
0
0
0
0
0
23
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
24
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
20
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
10
0
0
0
0
0
0
0
31
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
24
0
0
0
0
0
0
0
0
0
0

10
0
0
0
0
0
0
0
0
0
0
26
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
35
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
32
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
28
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
48
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
36
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
22
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
30
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
10
0
0
0
0
0
0
0
0
0
0
29
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
12
0
0
0
0
0
0
0
0
0
0
0
0
24
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
52
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
33
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
31
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
26
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
11
0
0
0
0
0
0
0
0
0
0
32
0
0
0
0
0
0
0
0
0
0
0
0
0

0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
26
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
49
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
28
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
40
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
23
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
23
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
19
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
42
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
38
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
37
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
36
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
23
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
25
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
28
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
40
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
18
0
0
0
0
0
0
0
0
0
0
0


...

0
0
0
0
0
0
30
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
35
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
53
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
35
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
52
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
47
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
27
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
38
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
32
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
51
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
42
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
40
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
23
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
42
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
42
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
76
0
0
0
0
0
0
0
0
0
0
0


0
0
0
0
0
0
0
0
0
0
17
0
0
0
0
0
0
0
0
0
0
0
0
44
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
34
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
30
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
30
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
34
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
35
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
47
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
36
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
32
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
33
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
21
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
29
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
29
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
32
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
38
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
27
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
22
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
31
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0

0
0
0
0
0
0
0
0
0
0
0
0
0
45
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
40
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
35
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
46
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
28
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
40
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
34
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
35
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
38
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
37
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
31
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
37
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
43
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
38
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
35
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
35
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0


0
0
0
0
0
0
0
0
32
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
53
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
58
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
32
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
41
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
39
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
32
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
26
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
41
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
39
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
39
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
32
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
46
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
36
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
37
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
31
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0


0
0
0
0
0
0
0
0
0
0
0
0
0
22
0
0
0
0
0
0
0
0
0
0
0
0
0
0
24
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
21
0
0
0
0
0
0
0
0
0
0
0
31
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
25
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
26
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
26
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
18
0
0
0
0
0
0
0
0
0
0
0
24
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
22
0
0
0
0
0
0
0
0
0
0
0
0
27
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
23
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
25
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
21
0
0
0
0
0
0
0
0
0
0
0
0
0
0
25
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
28
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
18
0
0
0
0
0
0
0
0
0
0
30
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
25
0
0
0
0
0
0
0
0
0
0
0
0
0
26
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
28
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
27
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
22
0
0
0
0
0
0
0
0
0
0
0
0
0
0
20
0
0
0
0
0
0
0
0
0
0
0
0
20
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
32
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
28
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
28
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
20

In [231]:
def calcAvg(df, embeddingmodel):
    import re
    for x in range(len(df)):   # for each product item 
        words = df.iloc[x,1].split()
        words_count = len(words)
        embedding_dim = 300
        embedding_matrix = np.zeros((words_count, embedding_dim))

        i = 0
        for word in words:
            embedding_vector = embeddingmodel.get(word)
            if embedding_vector is not None:
                embedding_matrix[i] = embedding_vector # Words not found in embedding index will be all-zeros
                i+=1
                print (embedding_matrix)
                
    dataframe=pd.DataFrame()
    dataframe.iloc[x] = embedding_matrix.mean(axis = 0) 
    return dataframe

In [229]:
def calcAvg(s, embeddingmodel):
    
        words =s.split()
        words_count = len(words)
        embedding_dim = 300
        embedding_matrix = np.zeros((words_count, embedding_dim))

        i = 0
        for word in words:
            embedding_vector = embeddingmodel.get(word)
            if embedding_vector is not None:
                embedding_matrix[i] = embedding_vector # Words not found in embedding index will be all-zeros
                i+=1
                return embedding_matrix.shape
#                 dataframe=pd.DataFrame()
#                 print(i)
#                 dataframe[x] = embedding_matrix.mean(axis = 0) 
#                 return dataframe

In [245]:
a = calcAvg(clothes, embeddingmodel)


AttributeError: 'DataFrame' object has no attribute 'split'

In [260]:
a.shape

(300, 1)

In [261]:
import numpy as np
import pandas as pd
import re

def data_cleaning(all_data,removeNa = True, keep_percent = False, rmPunctuation = True, rmNums = True, rmStopWords = True):
	
	all_data['alltext'] = all_data['alltext'].apply(lambda x: x.lower())
	
	if removeNa:
		all_data = all_data[all_data['alltext'].isnull() == False]


	if keep_percent:
		def replace_perc(str_perc):
			str_perc02 = re.sub('(\d+\%)\s*([a-z]+)','\\2\\1 \\2,', str_perc)
			return re.sub('([a-z]+)\s+(\d+\%)', '\\1\\2 \\1,', str_perc)

		all_data['alltext'] = all_data['alltext'].apply(replace_perc)

	if rmPunctuation:
		puncList = '!"#$&%\'()*+-,./:;<=>?@[\\]^_`{|}~'
		def rm_punc(s):
			s = re.sub('([a-z]+)\-([a-z]+)', '\\1\\2', s)
			for x in puncList:
				s=s.replace(x,' ')
			return s

		all_data['alltext'] = all_data['alltext'].apply(rm_punc)

	if rmNums:
		def rm_nums(s):
	#		s = re.sub('\s+\d+\s+', '', s)
			s = re.sub('\d+', '', s)
			return s

		all_data['alltext'] = all_data['alltext'].apply(rm_nums)

	if rmStopWords:
		def rm_stop(s):
			stop = ['ASOS', "YAS", "Ditsy", "Noisy", "May", "Ted","Baker", "River","Island", "Karen","Scott","PrettyLittleThing","Roxy","DESIGN","Chi", \
               "Alfani","Boohoo","Sofie","Schnoor","Ellesse", "Jeannie","TFNC","Sacred", "Hawk","Urban","Bliss","Puma","adidas", "Stella", \
               'cm', 'size', 'web id', 'approx', 'model', 'height', 'is', 'and', 'she', 'wearing', 'small', 'approximate', 'measurements', 'height', 'bust', 'waist', 'hips']
			
			lst = r'|'.join([x.lower() for x in stop])
			
			return re.sub(lst,'',s)


		# stop = ['ASOS', "YAS", "Ditsy", "Noisy", "May", "Ted","Baker", "River","Island", "Karen","Scott","PrettyLittleThing","Roxy","DESIGN","Chi",
  #              "Alfani","Boohoo","Sofie","Schnoor","Ellesse", "Jeannie","TFNC","Sacred", "Hawk","Urban","Bliss","Puma","adidas", "Stella"]
		# stop = [x.lower() for x in stop]

		all_data['alltext'] = all_data['alltext'].apply(rm_stop)


	return all_data





In [262]:
data_cleaning(clothes)

alltext  \
0      cotton tshirt tshirt in lightweight cotton jersey with a rounded hem  slightly longer at back  front  length       m                                                                                                                                                                                           
1      vneck jersey top longsleeved top in airy vcose jersey with a vneck  vcose                                                                                                                                                                                                                                      
2      jersey top with lace sleeveless top in soft vcose jersey with lace sections over shoulders  wide  gathered neckline front  back  vcose                                                                                                                                                                         
3      vneck top conscious  vneck top in airy jersey made from recycled polyester  buttons at top    length sleeves   a rounded hem with slits at sides  slightly longer at back  polyester                                                                                                                           
4      jersey camole top fit camole top in jersey with narrow shoulder straps  fit                                                                                                                                                                                                                                    
5      short tshirt short tshirt in soft jersey with contrasting trim at neckline  sleeves  cotton    polyester                                                                                                                                                                                                       
6      long tshirt long tshirt in jersey with sewn cuffs on sleeves  short sleeve                                                                                                                                                                                                                                     
7      tshirt fit tshirt in soft jersey  fit                                                                                                                                                                                                                                                                          
8      tshirt tshirt in soft  vcoseblend jersey  cotton    vcose                                                                                                                                                                                                                                                      
9      vneck camole top vneck camole top in soft vcose jersey  double layers of fabric at top  narrow shoulder straps   slits at sides of hem  lining  polyester                                                                                                                                                      
10     vneck jersey top short  fit top in cotton jersey with a vneck  short sleeves  fit                                                                                                                                                                                                                              
11     tshirt fit tshirt in soft jersey  fit                                                                                                                                                                                                                                                                          
12     vneck top top in woven fabric with vneck front  back  narrow shoulder straps  decorative straps at back  polyester                                                                                                                                        

In [263]:
import numpy as np
from scipy import spatial
import pandas as pd
import re

def loadGloveModel(gloveFile):
    print ("Loading Glove Model")
    f = open(gloveFile,'r',encoding="utf8")#
    model = {}
    for line in f:
        splitLine = line.split()
        word = splitLine[0]
        embedding = np.array([float(val) for val in splitLine[1:]])
        model[word] = embedding
        if len(model) % 19000== 0:
            print("+1")
    print ("Done.",len(model)," words loaded!")
    return model


def calcAvg(s,model, avgVec = True):
    words = s.split()
    words_count = len(words)
    embedding_dim = 300
    embedding_matrix = np.zeros((words_count, embedding_dim))
    i = 0
    for word in words:
        embedding_vector = model.get(word)

        if embedding_vector is not None:
            # Words not found in embedding index will be all-zeros.
            embedding_matrix[i] = embedding_vector
        i+=1

    if avgVec:
        return embedding_matrix.mean(axis = 0)
    else:
        return embedding_matrix

def similarity_score(df, i,j,model):
   # print (df.iloc[i,0])
    vec1 = calcAvg(df.iloc[i,0], model)
    vec2 = calcAvg(df.iloc[j,0], model)

    score = 1-spatial.distance.cosine(vec1,vec2)
    return score

def find_similar(df, i, model, count = 10):
    score_dic = {}
    for j in range(0, df.shape[0]):
        score_dic[j] = similarity_score(df,i,j, model)
    sorted_by_value = sorted(score_dic.items(), key=lambda kv: kv[1], reverse = True)
    return sorted_by_value[0:count]

In [278]:
new=find_similar(toy,5,embeddingmodel)

In [268]:
new

[(5, 1.0),
 (185, 1.0),
 (416, 1.0),
 (457, 1.0),
 (59, 0.9954583673723193),
 (443, 0.9941585044996504),
 (131, 0.980324909694367),
 (155, 0.980324909694367),
 (465, 0.980324909694367),
 (821, 0.9645576565671352)]

In [280]:
new #flatten the list

[(5, 1.0),
 (185, 1.0),
 (416, 1.0),
 (457, 1.0),
 (59, 0.9954081420533268),
 (443, 0.9927245681763929),
 (131, 0.982786959783819),
 (155, 0.982786959783819),
 (465, 0.982786959783819),
 (514, 0.9771956783429876)]